In [ ]:
!pip install transformers datasets torch pandas scikit-learn
!pip install transformers[torch] accelerate -U

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 547.8/547.8 kB 4.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.8/40.8 MB 13.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 11.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.9/64.9 kB 9.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 22.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 20.1 MB/s eta 0:00:00
  Using cached nvidia_cuda_nvrtc_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (23.7 MB)
  Using cached nvidia_cuda_runtime_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (823 kB)
  Using cached nvidia_cuda_cupti_cu12-12.1.105-py3-none-manylinux1_x86_64.whl (14.1 MB)
  Using cached nvidia_cudnn_cu12-8.9.2.26-py3-none-manylinux1_x86_64.whl (731.7 MB)
  Using cached nvidia_cublas_cu12-12.1.3.1-py3-none-manylinux1_x86_64.whl (410.6 MB)
  Using cached nvidia_cufft_cu12-11.0.2.54-py3-none-manylinux1_x86_64.whl 

In [ ]:
from datasets import load_dataset, concatenate_datasets
from transformers import BertTokenizer, BertForSequenceClassification, Trainer, TrainingArguments
from sklearn.metrics import accuracy_score, precision_recall_fscore_support
from sklearn.preprocessing import MultiLabelBinarizer
import torch
import numpy as np

# Load the dataset
dataset = load_dataset('joelniklaus/online_terms_of_service')

# Filter for English sentences only
dataset = dataset.filter(lambda x: x['language'] == 'en')

# Prepare the data: combine the individual boolean tags into a single label
def combine_labels(example):
    labels = ['a', 'ch', 'cr', 'j', 'law', 'ltd', 'ter', 'use', 'pinc']
    combined_label = [label for label in labels if example[label]]
    example['combined_label'] = combined_label
    return example

dataset = dataset.map(combine_labels)

# Split the dataset into train, validation, and test
train_data = dataset['train']
validation_data = dataset['validation']
test_data = dataset['test']

# Initialize the tokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')

# Create MultiLabelBinarizer
mlb = MultiLabelBinarizer()
# Concatenate datasets correctly
all_data = concatenate_datasets([train_data, validation_data, test_data])
all_labels = all_data['combined_label']
mlb.fit(all_labels)

def tokenize_and_encode_labels(examples):
    tokenized = tokenizer(examples['sentence'], padding='max_length', truncation=True)
    labels = mlb.transform(examples['combined_label'])
    tokenized['labels'] = torch.FloatTensor(labels)  # Convert labels to FloatTensor
    return tokenized

train_data = train_data.map(tokenize_and_encode_labels, batched=True)
validation_data = validation_data.map(tokenize_and_encode_labels, batched=True)
test_data = test_data.map(tokenize_and_encode_labels, batched=True)

train_data.set_format(type='torch', columns=['input_ids', 'attention_mask', 'labels'])
validation_data.set_format(type='torch', columns=['input_ids', 'attention_mask', 'labels'])
test_data.set_format(type='torch', columns=['input_ids', 'attention_mask', 'labels'])

# Load the model
num_labels = len(mlb.classes_)
model = BertForSequenceClassification.from_pretrained('bert-base-uncased', num_labels=num_labels, problem_type="multi_label_classification")

# Define training arguments
training_args = TrainingArguments(
    output_dir='./results',
    num_train_epochs=3,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    warmup_steps=500,
    weight_decay=0.01,
    logging_dir='./logs',
    logging_steps=10,
    evaluation_strategy="epoch"
)

# Define the compute metrics function
def compute_metrics(pred):
    labels = pred.label_ids
    preds = (pred.predictions > 0.5).astype(float)  # Convert to float
    precision, recall, f1, _ = precision_recall_fscore_support(labels, preds, average='micro')
    acc = accuracy_score(labels, preds)
    return {
        'accuracy': acc,
        'f1': f1,
        'precision': precision,
        'recall': recall
    }

# Initialize the Trainer
trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_data,
    eval_dataset=validation_data,
    compute_metrics=compute_metrics
)

# Train the model
trainer.train()

# Evaluate the model on validation data
validation_results = trainer.evaluate(eval_dataset=validation_data)
print(f"Validation Accuracy: {validation_results['eval_accuracy']}")

# Evaluate the model on test data
test_results = trainer.evaluate(eval_dataset=test_data)
print(f"Test Accuracy: {test_results['eval_accuracy']}")

# Save the model
model.save_pretrained('./tos-bert-classifier')
tokenizer.save_pretrained('./tos-bert-classifier')

# Save the MultiLabelBinarizer
import joblib
joblib.dump(mlb, './tos-bert-classifier/mlb.joblib')

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Generating train split:   0%|          | 0/19942 [00:00<?, ? examples/s]

Generating validation split:   0%|          | 0/1690 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/4297 [00:00<?, ? examples/s]

Filter:   0%|          | 0/19942 [00:00<?, ? examples/s]

...

model.safetensors:   0%|          | 0.00/440M [00:00<?, ?B/s]

Some weights of BertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier.bias', 'classifier.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.
/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1494: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
/usr/local/lib/python3.10/dist-packages/sklearn/metrics/_classification.py:1344: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Validation Accuracy: 0.9108433734939759
Test Accuracy: 0.928709055876686


['./tos-bert-classifier/mlb.joblib']

In [ ]:
import torch
from transformers import BertTokenizer, BertForSequenceClassification
import joblib

def load_model_and_tokenizer(model_path):
    model = BertForSequenceClassification.from_pretrained(model_path)
    tokenizer = BertTokenizer.from_pretrained(model_path)
    mlb = joblib.load(f"{model_path}/mlb.joblib")
    return model, tokenizer, mlb

def predict_clause(text, model, tokenizer, mlb):
    inputs = tokenizer(text, return_tensors="pt", truncation=True, padding=True, max_length=512)

    model.eval()

    with torch.no_grad():
        outputs = model(**inputs)

    probs = torch.sigmoid(outputs.logits).squeeze()
    predictions = (probs > 0.5).int().numpy()

    predicted_labels = mlb.classes_[predictions.astype(bool)]

    return predicted_labels, probs.numpy()

def determine_fairness(predicted_labels, probabilities, threshold=0.5):
    fairness_levels = {
        'clearly_fair': [],
        'potentially_unfair': [],
        'clearly_unfair': []
    }

    for label, prob in zip(predicted_labels, probabilities):
        if prob > threshold:
            if label in ['a', 'j', 'law']:
                fairness_levels['clearly_unfair'].append(label)
            elif label in ['ch', 'cr', 'ltd', 'ter', 'use', 'pinc']:
                fairness_levels['potentially_unfair'].append(label)

    if not fairness_levels['clearly_unfair'] and not fairness_levels['potentially_unfair']:
        return 'clearly_fair', []
    elif fairness_levels['clearly_unfair']:
        return 'clearly_unfair', fairness_levels['clearly_unfair']
    else:
        return 'potentially_unfair', fairness_levels['potentially_unfair']

model_path = './tos-bert-classifier'
model, tokenizer, mlb = load_model_and_tokenizer(model_path)

def test_model():
    while True:
        text = input("Enter a clause to classify (or 'quit' to exit): ")
        if text.lower() == 'quit':
            break

        predicted_labels, probabilities = predict_clause(text, model, tokenizer, mlb)
        fairness_level, unfair_labels = determine_fairness(mlb.classes_, probabilities)

        print("\nPredicted labels:")
        for label, prob in zip(mlb.classes_, probabilities):
            print(f"{label}: {prob:.4f}")

        print("\nClassified as:")
        for label in predicted_labels:
            print(f"- {label}")

        print(f"\nFairness level: {fairness_level}")
        if unfair_labels:
            print(f"Unfair labels: {', '.join(unfair_labels)}")
        print()

if __name__ == "__main__":
    test_model()

Enter a clause to classify (or 'quit' to exit): We reserve the right to suspend, terminate, or restrict your access to the platform at any time and for any reason, without prior notice or explanation. This includes but is not limited to violations of our community guidelines or terms of service, as determined solely by ConnectWorld.

Predicted labels:
a: 0.0418
ch: 0.2703
cr: 0.2862
j: 0.0229
law: 0.0394
ltd: 0.1806
pinc: 0.0391
ter: 0.6514
use: 0.0468

Classified as:
- ter

Fairness level: potentially_unfair
Unfair labels: ter

Enter a clause to classify (or 'quit' to exit): You have the right to use CommunityConnect for its intended purpose of connecting with others, sharing content responsibly, and engaging in constructive dialogue. You are responsible for the content you post and must respect the rights and privacy of others.

Predicted labels:
a: 0.0026
ch: 0.0041
cr: 0.0028
j: 0.0024
law: 0.0025
ltd: 0.0050
pinc: 0.0032
ter: 0.0038
use: 0.0053

Classified as:

Fairness level: cle

In [ ]:
!pip install huggingface_hub

In [ ]:
from transformers import BertForSequenceClassification, BertTokenizer
from huggingface_hub import HfApi, Repository
import os
import shutil

# Set your Hugging Face token and repo name
hf_token = "<Your HF Token>"
repo_name = "TOSBert"

# Set the path to your local model
local_model_path = "./tos-bert-classifier"

# Initialize Hugging Face API
api = HfApi()

# Create a new repository
repo_url = api.create_repo(
    repo_id=repo_name,
    token=hf_token,
    private=False,
    exist_ok=True
)

# Clone the empty repository
repo = Repository(local_dir=repo_name, clone_from=repo_url, use_auth_token=hf_token)

# Load your trained model and tokenizer
model = BertForSequenceClassification.from_pretrained(local_model_path)
tokenizer = BertTokenizer.from_pretrained(local_model_path)

# Save the model and tokenizer to the cloned repository
model.save_pretrained(repo_name)
tokenizer.save_pretrained(repo_name)

# Copy the label binarizer to the repository
shutil.copy(os.path.join(local_model_path, "mlb.joblib"), repo_name)

# Add a README file
with open(os.path.join(repo_name, "README.md"), "w") as f:
    f.write("# TOSBert\n\nThis model is trained to classify clauses in Terms of Service (ToS) documents.")

# Push the files to the Hugging Face Hub
repo.git_add()
repo.git_commit("Initial commit")
repo.git_push()

print(f"Model successfully pushed to https://huggingface.co/{repo_name}")

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:131: FutureWarning: 'Repository' (from 'huggingface_hub.repository') is deprecated and will be removed from version '1.0'. Please prefer the http-based alternatives instead. Given its large adoption in legacy code, the complete removal is only planned on next major release.
For more details, please read https://huggingface.co/docs/huggingface_hub/concepts/git_vs_http.
  warnings.warn(warning_message, FutureWarning)
Cloning https://huggingface.co/CodeHima/TOSBert into local empty directory.


Upload file model.safetensors:   0%|          | 1.00/418M [00:00<?, ?B/s]

Upload file mlb.joblib:   0%|          | 1.00/724 [00:00<?, ?B/s]

remote: -------------------------------------------------------------------------        
remote: Your push was accepted, but with warnings:         
remote: - Warning: empty or missing yaml metadata in repo card        
remote: help: https://huggingface.co/docs/hub/model-cards#model-card-metadata        
remote: -------------------------------------------------------------------------        
remote: -------------------------------------------------------------------------        
remote: Please find the documentation at:        
remote: https://huggingface.co/docs/hub/model-cards#model-card-metadata        
remote:         
remote: -------------------------------------------------------------------------        
To https://huggingface.co/CodeHima/TOSBert
   d1c057c..d6b0ebb  main -> main

remote: Your push was accepted, but with warnings:         
remote: - Warning: empty or missing yaml metadata in repo card        
remote: help: https://huggingface.co/docs/hub/model-cards#model-car

Model successfully pushed to https://huggingface.co/TOSBert
